In [0]:
import pyspark
import numpy as np
import pandas as pd

import  seaborn as sns
import matplotlib.pyplot as plt

import pyspark
import pandas as pd
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import pyspark.sql.functions as f
from pyspark.sql.functions import *
from pyspark.sql.functions import input_file_name
from pyspark.sql import DataFrame
from pyspark.sql import Window
from pyspark.sql.functions import sum,avg,max,min,mean,count
from pyspark.sql.functions import col, regexp_replace, split
from pyspark.sql.functions import col, create_map, lit, when
from pyspark.sql.functions import col, coalesce
from pyspark.sql.types import *;
from scipy.stats import *
from scipy import stats
from pyspark.sql.functions import col, sum
from pyspark.sql.functions import col, collect_list
from pyspark.sql.functions import regexp_replace

import gzip
# import StringIO --> ModuleNotFoundError: No module named 'StringIO'


from functools import reduce

# unificaion
from pyspark.sql.functions import col, concat, lit, lower, when

In [0]:
#-----------------------------------------------------------------------#
# Get Shape
#-----------------------------------------------------------------------#
def sparkShape(df):
    return (df.count(), len(df.columns))
pyspark.sql.dataframe.DataFrame.shape = sparkShape

#display(df_responses.shape())


#-----------------------------------------------------------------------#
# Append a list of dfs for selected columns
#-----------------------------------------------------------------------#
def append_dfs(dataframes: List[DataFrame], columns: List[str]) -> DataFrame:
    # Select columns
    df_union = dataframes[0].select(*columns)
    
    # Iterate and append all dfs
    for df in dataframes[1:]:
        df_selected = df.select(*columns)
        df_union = df_union.unionByName(df_selected)
    
    return df_union

#-----------------------------------------------------------------------#
# Replace spaces in column names
#-----------------------------------------------------------------------#
def remplazeSpacesInColumnName(df):
    columns = df.columns
    # Reemplazar espacios y puntos en los nombres de las columnas
    modified_columns = [col_name.replace(' ', '_').replace('.', '_') for col_name in columns]
    # Renombrar las columnas en el DataFrame
    renamed_df = df.select([col(col_name).alias(modified_col_name) for col_name, modified_col_name in zip(columns, modified_columns)])
    
    return renamed_df

#-----------------------------------------------------------------------#
# Calculate Null % for each column in df
#-----------------------------------------------------------------------#
def calcular_porcentaje_nulos(df):
    # Calcular el número de valores nulos por columna
    null_counts = df.select([sum(col(column).isNull().cast("int")).alias(column) for column in df.columns])
    
    # Convertir el DataFrame de recuento de nulos en un formato apilado
    expr_columns = ", ".join(["'{}', cast(`{}` as string)".format(col_name.replace(' ', '_'), col_name) for col_name in df.columns])
    stack_expr = "stack({num_columns}, {columns}) as (columna, valor)".format(
        num_columns=len(df.columns),
        columns=expr_columns
    )
    null_counts2 = null_counts.selectExpr(stack_expr)
    
    # Calcular el porcentaje de nulos por columna
    total_filas = df.count()
    null_counts2 = null_counts2.withColumn('percentage', (col('valor') / total_filas) * 100)
    
    return null_counts2
  
#-----------------------------------------------------------------------#
# Remove columns in df if Null % < percentage_threshold
#-----------------------------------------------------------------------#
def filter_columns_by_null_percentage(df_piv, df_null, percentage_threshold, column_to_keep_nulls_others):
    # Filtrar las columnas que cumplen el umbral de porcentaje
    columns_to_keep_nulls = df_null.filter(col("percentage") <= percentage_threshold) \
                                  .select(collect_list("columna")) \
                                  .first()[0]
                                  
    # Combinar las columnas adicionales con las columnas a mantener por el porcentaje de nulos
    columns_to_keep_nulls += column_to_keep_nulls_others

    #Preparar df antes de filtrar
    df_piv = remplazeSpacesInColumnName(df_piv)
    # Seleccionar solo las columnas que se van a mantener
    df_piv_filtered = df_piv.select(*[col(c) for c in df_piv.columns if c in columns_to_keep_nulls])
    
    return df_piv_filtered

#-----------------------------------------------------------------------#
# Add a prefix for a list of columns in df
#-----------------------------------------------------------------------#
def AddColumnPrefix(df, prefix, exclude_columns=[]):
    current_columns = df.columns
    # Lista de columnas a renombrar
    columns_to_rename = [col for col in current_columns if col not in exclude_columns]
    # Aplicar los cambios al DataFrame
    renamed_df = df.select([col(col_name).alias(prefix + col_name) if col_name in columns_to_rename else col(col_name) for col_name in current_columns])

    return renamed_df

In [0]:
#Funciones para manejar NULLS






##############



##############################


####################
def convertirDecimal(df, columns_to_exclude=[]):
    all_columns = df.columns
    columns_to_convert = [col_name for col_name in all_columns if col_name not in columns_to_exclude]
    
    # Aplicar la conversión a tipo decimal a las columnas seleccionadas
    for col_name in columns_to_convert:
        df = df.withColumn(col_name, df[col_name].cast("decimal"))
    # Completar los valores nulos con 0 en todas las columnas
    df = df.fillna(0)
    
    return df

######################
# Set 1 if value is not null in columns
def ColumntoFlag(df, excepciones):
    for columna in df.columns:
        if columna not in excepciones:
            df = df.withColumn(columna, when(col(columna).isNull() | (col(columna) == ""), 0).otherwise(1))
            df = df.withColumnRenamed(columna, columna)  # Mantener el mismo nombre de columna
    return df

In [0]:
storage_account_name = 'stgaclnrmlab'
storage_account_access_key = 'rf/4ogYc/eG+oqVD8K9xjsVamosf1qO1s0Kab+ujHsTt0GjaGY2XHfXFNVdti4iaUndCJjNSqizi+ASt8IWqHw=='
spark.conf.set('fs.azure.account.key.' + storage_account_name + '.blob.core.windows.net', storage_account_access_key)
blob_container = 'datasets'

path_2012 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2012_Cities_Climate_Hazards.csv"
path_2013 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2013_Cities_Climate_Hazards.csv"
path_2014 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2014_Cities_Climate_Hazards.csv"
path_2015 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2015_Cities_Climate_Hazards.csv"
path_2016 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2016_Cities_Climate_Hazards.csv"
path_2017 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2017_Cities_Climate_Hazards.csv"
path_2018 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2018_Cities_Climate_Hazards.csv"
path_2019 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2019_Cities_Climate_Hazards.csv"
path_2020 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2020_Cities_Climate_Hazards.csv"
path_2021 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2021_Cities_Climate_Hazards.csv"
path_2022 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2022_Cities_Climate_Hazards.csv"
path_2023 = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/Climate_Hazards/2023_Cities_Climate_Hazards.csv"


climate_hazards_2012 = spark.read.format("csv").load(path_2012, inferSchema = True, header = True)
climate_hazards_2013 = spark.read.format("csv").load(path_2013, inferSchema = True, header = True)
climate_hazards_2014 = spark.read.format("csv").load(path_2014, inferSchema = True, header = True)
climate_hazards_2015 = spark.read.format("csv").load(path_2015, inferSchema = True, header = True)
climate_hazards_2016 = spark.read.format("csv").load(path_2016, inferSchema = True, header = True)
climate_hazards_2017 = spark.read.format("csv").load(path_2017, inferSchema = True, header = True)
climate_hazards_2018 = spark.read.format("csv").load(path_2018, inferSchema = True, header = True)
climate_hazards_2019 = spark.read.format("csv").load(path_2019, inferSchema = True, header = True)
climate_hazards_2020 = spark.read.format("csv").load(path_2020, inferSchema = True, header = True)
climate_hazards_2021 = spark.read.format("csv").load(path_2021, inferSchema = True, header = True)
climate_hazards_2022 = spark.read.format("csv").load(path_2022, inferSchema = True, header = True)
climate_hazards_2023 = spark.read.format("csv").load(path_2023, inferSchema = True, header = True)

In [0]:
# Pivot column name to columns for 2018 dataset (only one that needs it)
climate_hazards_2018 = climate_hazards_2018.groupBy("Questionnaire", "Account Number", "Row Number") \
             .pivot("Column Name") \
             .agg({"Response Answer": "first"}) \
             .orderBy("Questionnaire", "Account Number", "Row Number")

In [0]:
# Rename columns
climate_hazards_2012 = climate_hazards_2012.withColumnRenamed("Account No", "account")\
.withColumnRenamed("Reporting Year", "year")\
.withColumnRenamed("Effects of Climate Change", "hazard")\
.withColumnRenamed("Risk Level", "hazard_magnitude")\
.withColumnRenamed("Risk Timescale", "hazard_timescale")
climate_hazards_2013 = climate_hazards_2013.withColumnRenamed("Account No", "account")\
.withColumnRenamed("Reporting Year", "year")\
.withColumnRenamed("Effects of Climate Change", "hazard")\
.withColumnRenamed("Risk Level", "hazard_magnitude")\
.withColumnRenamed("Risk Timescale", "hazard_timescale")
climate_hazards_2014 = climate_hazards_2014.withColumnRenamed("Account No", "account")\
.withColumnRenamed("Reporting Year", "year")\
.withColumnRenamed("Effects of Climate Change", "hazard")\
.withColumnRenamed("Risk Level", "hazard_magnitude")\
.withColumnRenamed("Risk Timescale", "hazard_timescale")
climate_hazards_2015 = climate_hazards_2015.withColumnRenamed("Account No", "account")\
.withColumnRenamed("Reporting Year", "year")\
.withColumnRenamed("Effects of climate change", "hazard")\
.withColumnRenamed("Magnitude", "hazard_magnitude")\
.withColumnRenamed("Anticipated timescale in years", "hazard_timescale")
climate_hazards_2016= climate_hazards_2016.withColumnRenamed("Account No", "account")\
.withColumnRenamed("Reporting Year", "year")\
.withColumnRenamed(" Climate hazards​", "hazard")\
.withColumnRenamed("Magnitude of impact", "hazard_magnitude")
climate_hazards_2017 = climate_hazards_2017.withColumnRenamed("Account number", "account")\
.withColumnRenamed("Project Year", "year")\
.withColumnRenamed("Climate Hazards", "hazard")\
.withColumnRenamed("Magnitude of Impact", "hazard_magnitude")
climate_hazards_2018 = climate_hazards_2018.withColumnRenamed("Questionnaire", "year")\
.withColumnRenamed("Account Number", "account")\
.withColumnRenamed("Anticipated timescale", "hazard_timescale")\
.withColumnRenamed("Climate Hazards", "hazard")\
.withColumnRenamed("Magnitude of impact", "hazard_magnitude")
climate_hazards_2019 = climate_hazards_2019.withColumnRenamed("Questionnaire Name", "year")\
.withColumnRenamed("Account Number", "account")\
.withColumnRenamed("Climate Hazards", "hazard")\
.withColumnRenamed("Current consequence of hazard", "hazard_magnitude")\
.withColumnRenamed("When do you first expect to experience those changes?", "hazard_timescale")
climate_hazards_2020 = climate_hazards_2020.withColumnRenamed("Questionnaire Name", "year")\
.withColumnRenamed("Account Number", "account")\
.withColumnRenamed("Climate Hazards", "hazard")\
.withColumnRenamed("Current magnitude of hazard", "hazard_magnitude")\
.withColumnRenamed("When do you first expect to experience those changes in frequency and intensity?", "hazard_timescale")
climate_hazards_2021 = climate_hazards_2021.withColumnRenamed("Questionnaire Name", "year")\
.withColumnRenamed("Account Number", "account")\
.withColumnRenamed("Climate Hazards", "hazard")\
.withColumnRenamed("Current magnitude of hazard", "hazard_magnitude")\
.withColumnRenamed("When do you first expect to experience those changes in frequency and intensity?", "hazard_timescale")
climate_hazards_2022 = climate_hazards_2022.withColumnRenamed("Reporting Year", "year")\
.withColumnRenamed("Organization Number", "account")\
.withColumnRenamed("Climate-related hazards", "hazard")\
.withColumnRenamed("Current magnitude of impact of hazard", "hazard_magnitude")\
.withColumnRenamed("Timeframe of expected future changes", "hazard_timescale")
climate_hazards_2023 = climate_hazards_2023.withColumnRenamed("Questionnaire", "year")\
.withColumnRenamed("Organization Number", "account")\
.withColumnRenamed("Climate-related hazards", "hazard")\
.withColumnRenamed("Current magnitude of impact of hazard", "hazard_magnitude")\
.withColumnRenamed("Timeframe of expected future changes", "hazard_timescale")

# Create missing columns 
climate_hazards_2016= climate_hazards_2016.withColumn("hazard_timescale", lit(None))
climate_hazards_2017 = climate_hazards_2017.withColumn("hazard_timescale", lit(None))


In [0]:
display(climate_hazards_2016)

Organisation Account No Country City Short Name C40 Reporting Year Climate hazards​ Magnitude of impact Impact description​ a) Asset or service b) Asset or service c) Asset or service City Location Country Location Jinja Municipal Council 62845 Uganda Jinja null 2016 Drought Serious Prolonged periods of dry weather with reduced precipitation, i.e. long dry seasons Energy Food and agriculture Health and community (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Air-borne disease Serious Air Emissions-smoke, particulate emission (dust) Health and community null null (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Atmospheric CO2 concentrations Extremely serious Fossil fuel use, wast burning and anaerobic putrefaction generate increasing quantities of CO2-cutting of trees without replacement Food and agriculture Health and community null (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Extreme hot days Serious Extreme hot days impact on human well being increasing heat , causing profuse sweating and reduced concentration at work. At night people sleep without covering themselves Health and community Food and agriculture null (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Hail Serious Impacts on crops and animals and may lead to death of humans Health and community Food and agriculture null (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Insect infestation Serious Impacts on crops and humans, through direct bites and cause of diseases Food and agriculture Health and community Education (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Lightning/thunderstorm Serious Causing accidents that destroy property and life Education Health and community Food and agriculture (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 River flood Serious Displacement of shoreline /riverbank activities/settlement/reielcauses reduced yields for wetland fringe agriculture, breakage of bridges Food and agriculture Transport Commerical (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Rain storm Serious Causes disconfort, accidents, ruins buildings, crops, flooding, may lead to loss of life and property. Transport Food and agriculture Health and community (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Vector-borne disease Extremely serious increase in vectors, mosquitoes, bed bugs, snails lead o upsurge of related diseases Health and community Food and agriculture Commerical (0.45021, 33.194542) (1.373333, 32.290275) Jinja Municipal Council 62845 Uganda Jinja null 2016 Water-borne disease Serious consumption of unsafe water increases morbidity of populations, reduced productivity and high cos of medicines Food and agriculture Health and community Water (0.45021, 33.194542) (1.373333, 32.290275) Egedal Municipality 62855 Denmark Egedal Municipality null 2016 Heavy snow Less serious null Food and agriculture Residential null (55.795045, 12.238733) (56.26392, 9.501785) Egedal Municipality 62855 Denmark Egedal Municipality null 2016 Flash/surface flood Serious null Transport Food and agriculture Residential (55.795045, 12.238733) (56.26392, 9.501785) Egedal Municipality 62855 Denmark Egedal Municipality null 2016 Rain storm Serious null Transport Food and agriculture Residential (55.795045, 12.238733) (56.26392, 9.501785) Egedal Municipality 62855 Denmark Egedal Municipality null 2016 Atmospheric CO2 concentrations Serious null Transport Food and agriculture Residential (55.795045, 12.238733) (56.26392, 9.501785) Egedal Municipality 62855 Denmark Egedal Municipality null 2016 Groundwater flood Serious null Residential Food and agriculture null

In [0]:
columns = ["account","year","hazard","hazard_magnitude","hazard_timescale"]

# Dfs to append
dataframes = [climate_hazards_2012,
climate_hazards_2013,
climate_hazards_2014,
climate_hazards_2015,
climate_hazards_2016,
climate_hazards_2017,
climate_hazards_2018,
climate_hazards_2019,
climate_hazards_2020,
climate_hazards_2021,
climate_hazards_2022,
climate_hazards_2023]

# Append all dfs
climate_hazards = append_dfs(dataframes, columns)

In [0]:
# Extract year
climate_hazards = climate_hazards.withColumn("year", regexp_replace("year", "Cities ", ""))

# Filter wrong rows
climate_hazards = climate_hazards.filter(col("account").isNotNull())
years = ["2012", "2013", "2014", "2015", "2016", "2017", "2018", "2019", "2020", "2021", "2022", "2023"]
climate_hazards = climate_hazards.filter(col("year").isin(years))

# Add unique id
climate_hazards = climate_hazards.withColumn("account_year", concat(climate_hazards["account"], lit("_"), climate_hazards["year"]))

In [0]:
display(climate_hazards.select("hazard").distinct())

hazard Other: Plague increase Increased frequency of large storms Other: Drier Summers Other: -	Flood volume will increase by the same percentage as precipitation, but flood peak discharge will increase more. Other: Increased frequency of floods Other: Severe weather events: Heavy Rain; Thunderstorms; Tropical Cyclones Other: Frost Other: Other: Decrease in the predictability of seasonal weather Other: -	Flood-prone area will expand in the future Warmer water temperatures Other: All of the above Other: More frequent and intense Wildfires Increased risk of storm surges Other: Less freezes Other: Diminished Air Quality Other: More landslides Other: Increase in number of tropical diseases Other: More intense precipitation Change in seasonality of rainfall Sea level rise Increased wind speeds Other: Rise in temperature Other: More frequent floods Other: Sources Cited Reduced average annual rainfall Other: More storms with increased wind speed Reduced average annual snowfall Other: Increased health risk associated with Malaria and Water Bourne Diseases More frequent rainfall More hot days Other: Increased annual average temperature More intense droughts Other: Increase in mosquito-borne diseases, Limited of Clean Water, Lost of Job Opportunity Other: Milder Winters Increased average annual rainfall Increased urban heat island effect Other: Increase in average temperature Other: Increase in rainfall Other: -	The local mean temperature will rise by 1.9oC and 1.2oC Other: -	The sea level in the Gulf of Thailand will rise by 0.29 and 0.19 meters corresponding to IPCC A1FI and B1 climate scenarios Hotter summers Other: Decrease Air Quality Other: Thermal anomalies: increase and decrease of temperature due to global phenomena such as El Niño and La Niña. Other: Rise in mean sea level More frequent droughts More frequent heatwaves Other: Increase in extreme precipitation events Other: Water level drop in Great Lakes Basin Other: Increased average annual rainfall variability Other: -	Storm surges are important, but will have less effect on flooding. Other: -	The basin mean precipitation will rise by 3 and 2% corresponding to IPCC A1FI and B1 climate scenarios (SRES -Special Reports on Emissions Scenarios) respectively More intense rainfall More intense heatwaves Other: Observed Risks Other: Incremento en las temperaturas Extremas Other: Hotter winters Other: •	The basin mean precipitation will rise by 2-3% corresponding to IPCC A1FI and B1 climate scenarios (SRES -Special Reports on Emissions Scenarios) respectively Other: Increased hail danger Other: Olas de calor Other: Allergenic pollens increase. Other: Extreme weather events Other: Colder - longer winters Other: More intense and frequent yellow dust Other: Elevation of rainwater acidification Other: Increase in average monthly daily minimun temperatures Other: Increase in average monthly daily maximun temperatures Other: Wild Fire Other: •	Flood volume will increase by the same percentage as precipitation, but flood peak discharge will increase more. Other: Contaminación del aire Other: •	The local mean temperature will rise by 1.2-1.9 oC Other: Floodwater Other: •	The sea level in the Gulf of Thailand will rise by 0.19-0.29 meters corresponding to IPCC A1FI and B1 climate scenarios More intense heat waves Other: NOx exceedances (greenhouse effect gas) Other: Increase of intense rainfalls Other: Landslides and erosion Other: •	Flood-prone area will expand in the future Other: Flooding Other: Occurrence of floods and inundation Other: Susceptibility to cold waves Other: Reducción en disponibilidad hídrica. Other: Extreme weather/storm events Other: Incremento de la disponibilidad hídrica en áreas de pendiente con alto grado de deforestación o pérdida de ecosistemas naturales presentan alto grado de exposición a deslizamientos. Other: Lower lake levels Other: Potable water scarcity Other: Enfermedades transmitidas por vectores Other: •	Storm surges are important, but will have less effe

In [0]:
# Normalize categories
climate_hazards = climate_hazards.withColumn("hazard", 
            when((upper(col("hazard")).like("%ENFERM%")) 
                 | (upper(col("hazard")).like("%DISEASE%"))
                 | (upper(col("hazard")).like("%ILLN%"))
                 | (upper(col("hazard")).like("%INFLUEN%"))
                 | (upper(col("hazard")).like("%ALLERG%"))
                 | (upper(col("hazard")).like("%POLLEN%")), 'Disease')
            .when((upper(col("hazard")).like("%INFEST%"))
                 | (upper(col("hazard")).like("%INVAS%"))
                 | (upper(col("hazard")).like("%PEST%"))
                 | (upper(col("hazard")).like("%PLAG%")), 'Insect infestation')
            .when((upper(col("hazard")).like("%BIO%")), 'Other biological')
            .when((upper(col("hazard")).like("%ATMOS%"))
                 | (upper(col("hazard")).like("%CO2%")), 'Atmospheric CO2 concentrations')
            .when((upper(col("hazard")).like("%AIR%")), 'Air pollution')
            .when((upper(col("hazard")).like("%OCEAN%")), 'Ocean acidification')
            .when((upper(col("hazard")).like("%INTRUSI%"))
                 | (upper(col("hazard")).like("%SALIN%")), 'Salt water intrusion')  
            .when((upper(col("hazard")).like("%RAIN%"))
                 | (upper(col("hazard")).like("%LLUVIA%"))
                 | (upper(col("hazard")).like("%PRECIP%"))
                 | (upper(col("hazard")).like("%MONSOON%"))
                 | (upper(col("hazard")).like("%HAIL%"))
                 | (upper(col("hazard")).like("%GRANIZ%"))
                 | (upper(col("hazard")).like("%FOG%"))
                 | (upper(col("hazard")).like("%NIEB%")), 'Heavy precipitation')
            .when((upper(col("hazard")).like("%SNOW%"))
                 | (upper(col("hazard")).like("%NEVA%"))
                 | (upper(col("hazard")).like("%NIEVE%")), 'Heavy snow')
            .when((upper(col("hazard")).like("%COLD%"))
                 | (upper(col("hazard")).like("%FREEZ%"))
                 | (upper(col("hazard")).like("%FRÍO%"))
                 | (upper(col("hazard")).like("%FROST%"))
                 | (upper(col("hazard")).like("%HELAD%"))
                 | (upper(col("hazard")).like("%IVERN%"))
                 | (upper(col("hazard")).like("%WINTER%")), 'Extreme cold')
            .when((upper(col("hazard")).like("%CALOR%"))
                 | (upper(col("hazard")).like("%CALUR%"))
                 | (upper(col("hazard")).like("%HEAT%"))
                 | (upper(col("hazard")).like("%HIGH%"))
                 | (upper(col("hazard")).like("%HOT%"))
                 | (upper(col("hazard")).like("%TEMP%"))
                 | (upper(col("hazard")).like("%WARM%")), 'Extreme heat')
            .when((upper(col("hazard")).like("%WEATHE%"))
                 | (upper(col("hazard")).like("%CLIMA%")), 'Extreme weather')
            .when((upper(col("hazard")).like("%SUPERF%"))
                 | (upper(col("hazard")).like("%SURFACE%")), 'Flash/surface flood')
            .when((upper(col("hazard")).like("%GROUNDWATER%"))
                 | (upper(col("hazard")).like("%SUBTERR%")), 'Groundwater flood')
            .when((upper(col("hazard")).like("%RIVER%"))
                 | (upper(col("hazard")).like("%FLUVIAL%")), 'River flood')
            .when((upper(col("hazard")).like("%COASTAL%"))
                 | (upper(col("hazard")).like("%MAR%"))
                 | (upper(col("hazard")).like("%SEE%"))
                 | (upper(col("hazard")).like("%SEA LEVEL RISE%")), 'Coastal flood')
            .when((upper(col("hazard")).like("%FLOOD%"))
                 | (upper(col("hazard")).like("%INUND%"))
                 | (upper(col("hazard")).like("%PLUVIAL%")), 'Other flood')
            .when((upper(col("hazard")).like("%AVALAN%")), 'Avalanche')
            .when((upper(col("hazard")).like("%SUBSIDEN%")), 'Subsidence')
            .when((upper(col("hazard")).like("%LANDSL%"))
                 | (upper(col("hazard")).like("%DESLIZ%"))
                 | (upper(col("hazard")).like("%DESLAV%"))
                 | (upper(col("hazard")).like("%ROCK%"))
                 | (upper(col("hazard")).like("%ROCA%"))
                 | (upper(col("hazard")).like("%MASS%")), 'Landslide')
            .when((upper(col("hazard")).like("%SOIL%"))
                 | (upper(col("hazard")).like("%EROSI%")), 'Soil degradation/erosion')
            .when((upper(col("hazard")).like("%CYCLON%"))
                 | (upper(col("hazard")).like("%HURAC%"))
                 | (upper(col("hazard")).like("%TORNADO%")), 'Cyclone/Hurricane/Tornado')
            .when((upper(col("hazard")).like("%WIDN%"))
                 | (upper(col("hazard")).like("%VIENT%")), 'Extreme wind')
            .when((upper(col("hazard")).like("%STORM%"))
                 | (upper(col("hazard")).like("%TORMENT%"))
                 | (upper(col("hazard")).like("%EXTRA%")), 'Storm')
            .when((upper(col("hazard")).like("%DROUGHT%"))
                 | (upper(col("hazard")).like("%SEQU%"))
                 | (upper(col("hazard")).like("%DESERT%"))
                 | (upper(col("hazard")).like("%DRY%"))
                 | (upper(col("hazard")).like("%ESCAZES%")), 'Drought')
            .when((upper(col("hazard")).like("%WATER%"))
                 | (upper(col("hazard")).like("%AGUA%")), 'Water stress')
            .when((upper(col("hazard")).like("%FIRE%"))
                 | (upper(col("hazard")).like("%FUEGO%"))
                 | (upper(col("hazard")).like("%INCEND%")), 'Wildfire')
            .when(col("hazard").isNull(), None)
            .otherwise('Other'))

climate_hazards = climate_hazards.withColumn("hazard_group", 
            when((upper(col("hazard")).like("%ENFERM%")) 
                 | (upper(col("hazard")).like("%DISEASE%"))
                 | (upper(col("hazard")).like("%ILLN%"))
                 | (upper(col("hazard")).like("%INFLUEN%"))
                 | (upper(col("hazard")).like("%ALLERG%"))
                 | (upper(col("hazard")).like("%POLLEN%"))
                 | (upper(col("hazard")).like("%INFEST%"))
                 | (upper(col("hazard")).like("%INVAS%"))
                 | (upper(col("hazard")).like("%PEST%"))
                 | (upper(col("hazard")).like("%PLAG%"))
                 | (upper(col("hazard")).like("%BIO%")), 'Biological')
            .when((upper(col("hazard")).like("%ATMOS%"))
                 | (upper(col("hazard")).like("%CO2%"))
                 | (upper(col("hazard")).like("%AIR%"))
                 | (upper(col("hazard")).like("%OCEAN%"))
                 | (upper(col("hazard")).like("%INTRUSI%"))
                 | (upper(col("hazard")).like("%SALIN%")), 'Chemical change')
            .when((upper(col("hazard")).like("%RAIN%"))
                 | (upper(col("hazard")).like("%LLUVIA%"))
                 | (upper(col("hazard")).like("%PRECIP%"))
                 | (upper(col("hazard")).like("%MONSOON%"))
                 | (upper(col("hazard")).like("%HAIL%"))
                 | (upper(col("hazard")).like("%GRANIZ%"))
                 | (upper(col("hazard")).like("%FOG%"))
                 | (upper(col("hazard")).like("%NIEB%"))
                 | (upper(col("hazard")).like("%SNOW%"))
                 | (upper(col("hazard")).like("%NEVA%"))
                 | (upper(col("hazard")).like("%NIEVE%")), 'Extreme Precipitation')
            .when((upper(col("hazard")).like("%COLD%"))
                 | (upper(col("hazard")).like("%FREEZ%"))
                 | (upper(col("hazard")).like("%FRÍO%"))
                 | (upper(col("hazard")).like("%FROST%"))
                 | (upper(col("hazard")).like("%HELAD%"))
                 | (upper(col("hazard")).like("%IVERN%"))
                 | (upper(col("hazard")).like("%WINTER%"))
                 | (upper(col("hazard")).like("%CALOR%"))
                 | (upper(col("hazard")).like("%CALUR%"))
                 | (upper(col("hazard")).like("%HEAT%"))
                 | (upper(col("hazard")).like("%HIGH%"))
                 | (upper(col("hazard")).like("%HOT%"))
                 | (upper(col("hazard")).like("%TEMP%"))
                 | (upper(col("hazard")).like("%WARM%"))
                 | (upper(col("hazard")).like("%WEATHE%"))
                 | (upper(col("hazard")).like("%CLIMA%")), 'Extreme temperatures')
            .when((upper(col("hazard")).like("%SUPERF%"))
                 | (upper(col("hazard")).like("%SURFACE%"))
                 | (upper(col("hazard")).like("%GROUNDWATER%"))
                 | (upper(col("hazard")).like("%SUBTERR%"))
                 | (upper(col("hazard")).like("%RIVER%"))
                 | (upper(col("hazard")).like("%FLUVIAL%"))
                 | (upper(col("hazard")).like("%COASTAL%"))
                 | (upper(col("hazard")).like("%MAR%"))
                 | (upper(col("hazard")).like("%SEE%"))
                 | (upper(col("hazard")).like("%SEA LEVEL RISE%"))
                 | (upper(col("hazard")).like("%FLOOD%"))
                 | (upper(col("hazard")).like("%INUND%"))
                 | (upper(col("hazard")).like("%PLUVIAL%")), 'Flood and sea level rise')
            .when((upper(col("hazard")).like("%AVALAN%"))
                 | (upper(col("hazard")).like("%SUBSIDEN%"))
                 | (upper(col("hazard")).like("%LANDSL%"))
                 | (upper(col("hazard")).like("%DESLIZ%"))
                 | (upper(col("hazard")).like("%DESLAV%"))
                 | (upper(col("hazard")).like("%ROCK%"))
                 | (upper(col("hazard")).like("%ROCA%"))
                 | (upper(col("hazard")).like("%MASS%"))
                 | (upper(col("hazard")).like("%SOIL%"))
                 | (upper(col("hazard")).like("%EROSI%")), 'Mass movement ')
            .when((upper(col("hazard")).like("%CYCLON%"))
                 | (upper(col("hazard")).like("%HURAC%"))
                 | (upper(col("hazard")).like("%TORNADO%"))
                 | (upper(col("hazard")).like("%WIDN%"))
                 | (upper(col("hazard")).like("%VIENT%"))
                 | (upper(col("hazard")).like("%STORM%"))
                 | (upper(col("hazard")).like("%TORMENT%"))
                 | (upper(col("hazard")).like("%EXTRA%")), 'Storm and wind')
            .when((upper(col("hazard")).like("%DROUGHT%"))
                 | (upper(col("hazard")).like("%SEQU%"))
                 | (upper(col("hazard")).like("%DESERT%"))
                 | (upper(col("hazard")).like("%DRY%"))
                 | (upper(col("hazard")).like("%ESCAZES%"))
                 | (upper(col("hazard")).like("%WATER%"))
                 | (upper(col("hazard")).like("%AGUA%")), 'Water scarcity')
            .when((upper(col("hazard")).like("%FIRE%"))
                 | (upper(col("hazard")).like("%FUEGO%"))
                 | (upper(col("hazard")).like("%INCEND%")), 'Wildfire')
            .when(col("hazard").isNull(), None)
            .otherwise('Other'))

climate_hazards = climate_hazards.withColumn("hazard_magnitude", 
            when((upper(col("hazard_magnitude")) == "SERIOUS") | (upper(col("hazard_magnitude")) == "MEDIUM HIGH"), '3')
            .when((upper(col("hazard_magnitude")).like("%MEDIUM%")), '2')
            .when((upper(col("hazard_magnitude")).like("%HIGH%")) | (upper(col("hazard_magnitude")).like("%EXTREME%")), '4')
            .when((upper(col("hazard_magnitude")).like("%LOW%")) | (upper(col("hazard_magnitude")).like("%LESS%")), '1')
            .when((upper(col("hazard_magnitude")).like("%NOT%")), '0')
            .when(col("hazard_magnitude").isNull(), None)
            .otherwise('0'))

climate_hazards = climate_hazards.withColumn("hazard_timescale", 
          when((upper(col("hazard_timescale")).like("%IMMEDIATELY%")) | (upper(col("hazard_timescale")).like("%CURRENT%")) | (upper(col("hazard_timescale")).like("%ALREADY%")) | (upper(col("hazard_timescale")).like("%INTERMITTENLY%")), '4')
          .when((upper(col("hazard_timescale")).like("%SHORT%")) | (upper(col("hazard_timescale")).like("%HIGH%")), '3')
          .when((upper(col("hazard_timescale")).like("%MEDIUM%")), '2')
          .when((upper(col("hazard_timescale")).like("%LONG%")) | (upper(col("hazard_timescale")).like("%LOW%")), '1')
          .when(col("hazard_timescale").isNull(), None)
          .otherwise('0'))

In [0]:
display(climate_hazards)

account_year account year hazard_group hazard hazard_count hazard_magnitude_avg hazard_magnitude_sum hazard_timescale_avg hazard_timescale_sum 20113_2012 20113 2012 Extreme Precipitation Heavy precipitation 1 1.0 1.0 4.0 4.0 31108_2012 31108 2012 Extreme temperatures Extreme heat 3 3.0 9.0 4.0 12.0 31009_2012 31009 2012 Extreme Precipitation Heavy precipitation 1 3.0 3.0 3.0 3.0 31114_2012 31114 2012 Flood and sea level rise Coastal flood 1 4.0 4.0 2.0 2.0 35870_2012 35870 2012 Storm and wind Storm 1 4.0 4.0 4.0 4.0 3417_2012 3417 2012 Storm and wind Storm 1 4.0 4.0 4.0 4.0 31108_2012 31108 2012 Water scarcity Drought 1 3.0 3.0 4.0 4.0 37261_2012 37261 2012 Extreme Precipitation Heavy precipitation 1 4.0 4.0 4.0 4.0 31182_2012 31182 2012 Flood and sea level rise Coastal flood 1 3.0 3.0 2.0 2.0 31446_2012 31446 2012 Extreme Precipitation Heavy precipitation 1 1.0 1.0 2.0 2.0 31313_2012 31313 2012 Flood and sea level rise Coastal flood 1 3.0 3.0 1.0 1.0 31180_2012 31180 2012 Extreme temperatures Extreme heat 2 3.0 6.0 2.0 4.0 35874_2012 35874 2012 Extreme Precipitation Heavy precipitation 2 3.0 6.0 2.0 4.0 31112_2012 31112 2012 Water scarcity Drought 1 3.0 3.0 1.0 1.0 31150_2012 31150 2012 Flood and sea level rise Other flood 2 0.0 0.0 1.0 2.0 31180_2012 31180 2012 Water scarcity Drought 1 3.0 3.0 3.0 3.0 36426_2012 36426 2012 Other Other 1 3.0 3.0 4.0 4.0 3422_2012 3422 2012 Extreme temperatures Extreme heat 4 3.0 12.0 4.0 16.0 31446_2012 31446 2012 Extreme temperatures Extreme heat 2 1.0 2.0 2.0 4.0 31184_2012 31184 2012 Flood and sea level rise Other flood 1 null null 3.0 3.0 3429_2012 3429 2012 Flood and sea level rise Coastal flood 1 4.0 4.0 1.0 1.0 35874_2012 35874 2012 Water scarcity Drought 1 3.0 3.0 2.0 2.0 31166_2012 31166 2012 Extreme temperatures Extreme heat 1 3.0 3.0 4.0 4.0 35868_2012 35868 2012 Extreme temperatures Extreme heat 1 1.0 1.0 3.0 3.0 8242_2012 8242 2012 Other Other 1 1.0 1.0 2.0 2.0 36252_2012 36252 2012 Extreme Precipitation Heavy precipitation 1 1.0 1.0 3.0 3.0 31090_2012 31090 2012 Storm and wind Storm 1 4.0 4.0 3.0 3.0 31111_2012 31111 2012 Extreme Precipitation Heavy precipitation 5 null null 2.5 5.0 31155_2012 31155 2012 Flood and sea level rise Other flood 1 4.0 4.0 4.0 4.0 35884_2012 35884 2012 Extreme temperatures Extreme heat 2 2.0 4.0 3.5 7.0 37261_2012 37261 2012 Extreme temperatures Extreme heat 1 4.0 4.0 4.0 4.0 31109_2012 31109 2012 Storm and wind Storm 1 3.0 3.0 4.0 4.0 35870_2012 35870 2012 Flood and sea level rise Coastal flood 1 4.0 4.0 4.0 4.0 35863_2012 35863 2012 Extreme Precipitation Heavy precipitation 1 4.0 4.0 2.0 2.0 31174_2012 31174 2012 Water scarcity Drought 2 1.0 2.0 2.0 4.0 1184_2012 1184 2012 Extreme Precipitation Heavy precipitation 3 3.0 9.0 1.6666666666666667 5.0 35393_2012 35393 2012 Storm and wind Storm 1 3.0 3.0 3.0 3.0 31155_2012 31155 2012 Flood and sea level rise Coastal flood 1 3.0 3.0 3.0 3.0 32550_2012 32550 2012 Water scarcity Drought 1 4.0 4.0 3.0 3.0 31117_2012 31117 2012 Water scarcity Water stress 1 3.0 3.0 0.0 0.0 35863_2012 35863 2012 Flood and sea level rise Coastal flood 1 3.0 3.0 1.0 1.0 14874_2012 14874 2012 Extreme Precipitation Heavy precipitation 1 3.0 3.0 3.0 3.0 31186_2012 31186 2012 Water scarcity Drought 1 1.0 1.0 4.0 4.0 31185_2012 31185 2012 Extreme Precipitation Heavy precipitation 1 3.0 3.0 4.0 4.0 35868_2012 35868 2012 Extreme Precipitation Heavy precipitation 1 1.0 1.0 3.0 3.0 31090_2012 31090 2012 Flood and sea level rise Coastal flood 1 1.0 1.0 3.0 3.0 31150_2012 31150 2012 Extreme temperatures Extreme heat 1 0.0 0.0 1.0 1.0 14874_2012 14874 2012 Extreme Precipitation Heavy snow 1 1.0 1.0 3.0 3.0 31148_2012 31148 2012 Flood and sea level rise Coastal flood 1 3.0 3.0 1.0 1.0 31111_2012 31111 2012 Flood and sea level rise Coastal flood 1 null null 1.0 1.0 31184_2012 31184 2012 Biological Disease 1 null null 3.0 3.0 31166_2012 31166 2012 Biological Disease 1 3.0 3.0 4.0 4.0 31150_2012 31150 2012 Extreme Precipitation Heavy precipitati

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:

# Group by categorical columns according to new categories defined earlier
climate_hazards = climate_hazards.groupBy('account_year', 'account', 'year', 'hazard_group', 'hazard').agg(
    count('*').alias('hazard_count'), 
    avg('hazard_magnitude').alias('hazard_magnitude_avg'),
    sum('hazard_magnitude').alias('hazard_magnitude_sum'),
    avg('hazard_timescale').alias('hazard_timescale_avg'),
    sum('hazard_timescale').alias('hazard_timescale_sum')
)

# Generate General measures
climate_hazards_1 = climate_hazards.groupBy('account_year', 'account', 'year') \
    .agg(
    count('*').alias('hazard_count'), 
    avg('hazard_magnitude_avg').alias('hazard_magnitude_avg'),
    sum('hazard_magnitude_sum').alias('hazard_magnitude_sum'),
    avg('hazard_timescale_avg').alias('hazard_timescale_avg'),
    sum('hazard_timescale_sum').alias('hazard_timescale_sum'))

# Generate Specific measures by hazard_group
climate_hazards_2 = climate_hazards.groupBy('account_year').pivot('hazard_group') \
    .agg(first('hazard_count').alias('count'), 
         first('hazard_magnitude_avg').alias('magnitude_avg'), 
         first('hazard_magnitude_sum').alias('magnitude_sum'), 
         first('hazard_timescale_avg').alias('timescale_avg'), 
         first('hazard_timescale_sum').alias('timescale_sum')
    )

# Normalize column names
climate_hazards_2 = remplazeSpacesInColumnName(climate_hazards_2)

In [0]:
# Calculate null % for each column
climate_hazards_2_nulls = calcular_porcentaje_nulos(climate_hazards_2)

# Remove columnas with null % < percentage_threshold
percentage_threshold = 51
column_to_keep_nulls_others = []

climate_hazards_2 = filter_columns_by_null_percentage(climate_hazards_2, climate_hazards_2_nulls, percentage_threshold, column_to_keep_nulls_others)

display(climate_hazards_2_nulls)

columna valor percentage account_year 0 0.0 null_count 5806 91.54840744244717 null_magnitude_avg 6296 99.27467675812046 null_magnitude_sum 6296 99.27467675812046 null_timescale_avg 6332 99.84232103437401 null_timescale_sum 6332 99.84232103437401 Biological_count 5066 79.88016398612426 Biological_magnitude_avg 5103 80.4635761589404 Biological_magnitude_sum 5103 80.4635761589404 Biological_timescale_avg 5401 85.16240933459477 Biological_timescale_sum 5401 85.16240933459477 Chemical_change_count 5748 90.63386944181646 Chemical_change_magnitude_avg 5769 90.96499526963103 Chemical_change_magnitude_sum 5769 90.96499526963103 Chemical_change_timescale_avg 5943 93.70860927152319 Chemical_change_timescale_sum 5943 93.70860927152319 Extreme_Precipitation_count 3140 49.51119520655944 Extreme_Precipitation_magnitude_avg 3234 50.993377483443716 Extreme_Precipitation_magnitude_sum 3234 50.993377483443716 Extreme_Precipitation_timescale_avg 3741 58.98770104068117 Extreme_Precipitation_timescale_sum 3741 58.98770104068117 Extreme_temperatures_count 2206 34.783979817092394 Extreme_temperatures_magnitude_avg 2329 36.72343109429202 Extreme_temperatures_magnitude_sum 2329 36.72343109429202 Extreme_temperatures_timescale_avg 3053 48.13938820561337 Extreme_temperatures_timescale_sum 3053 48.13938820561337 Flood_and_sea_level_rise_count 2474 39.00977609586881 Flood_and_sea_level_rise_magnitude_avg 2592 40.87038789025544 Flood_and_sea_level_rise_magnitude_sum 2592 40.87038789025544 Flood_and_sea_level_rise_timescale_avg 3374 53.20088300220751 Flood_and_sea_level_rise_timescale_sum 3374 53.20088300220751 Mass_movement__count 5355 84.43708609271523 Mass_movement__magnitude_avg 5387 84.94165878271839 Mass_movement__magnitude_sum 5387 84.94165878271839 Mass_movement__timescale_avg 5609 88.44213181961527 Mass_movement__timescale_sum 5609 88.44213181961527 Other_count 5604 88.36329233680227 Other_magnitude_avg 5645 89.00977609586882 Other_magnitude_sum 5645 89.00977609586882 Other_timescale_avg 5794 91.359192683696 Other_timescale_sum 5794 91.359192683696 Storm_and_wind_count 4526 71.36549984232103 Storm_and_wind_magnitude_avg 4577 72.16966256701356 Storm_and_wind_magnitude_sum 4577 72.16966256701356 Storm_and_wind_timescale_avg 4960 78.20876695048881 Storm_and_wind_timescale_sum 4960 78.20876695048881 Water_scarcity_count 3528 55.62913907284768 Water_scarcity_magnitude_avg 3610 56.92210659098076 Water_scarcity_magnitude_sum 3610 56.92210659098076 Water_scarcity_timescale_avg 4107 64.75875118259225 Water_scarcity_timescale_sum 4107 64.75875118259225 Wildfire_count 5443 85.8246609902239 Wildfire_magnitude_avg 5468 86.21885840428887 Wildfire_magnitude_sum 5468 86.21885840428887 Wildfire_timescale_avg 5714 90.09776095868811 Wildfire_timescale_sum 5714 90.09776095868811

In [0]:
#Join columns to prepare final df for this question group
df_climate_hazards = climate_hazards_1.join(climate_hazards_2, on='account_year')

# Fill Nulls with 0
df_climate_hazards = df_climate_hazards.na.fill(0)


df_climate_hazards = AddColumnPrefix(df_climate_hazards, "hazard_", exclude_columns=['account_year',
'account',
'year',
'hazard_count',
'hazard_magnitude_avg',
'hazard_magnitude_sum',
'hazard_timescale_avg',
'hazard_timescale_sum'])



In [0]:
display(df_climate_hazards)

account_year account year hazard_count hazard_magnitude_avg hazard_magnitude_sum hazard_timescale_avg hazard_timescale_sum Extreme_Precipitation_count Extreme_Precipitation_magnitude_avg Extreme_Precipitation_magnitude_sum Extreme_temperatures_count Extreme_temperatures_magnitude_avg Extreme_temperatures_magnitude_sum Extreme_temperatures_timescale_avg Extreme_temperatures_timescale_sum Flood_and_sea_level_rise_count Flood_and_sea_level_rise_magnitude_avg Flood_and_sea_level_rise_magnitude_sum 849043_2020 849043 2020 3 2.0 6.0 2.6666666666666665 8.0 1 2.0 2.0 1 2.0 2.0 3.0 3.0 0 0.0 0.0 55159_2021 55159 2021 1 0.0 0.0 0.0 0.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 0 0.0 0.0 859093_2021 859093 2021 1 0.0 0.0 0.0 0.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 0 0.0 0.0 50387_2017 50387 2017 1 0.0 0.0 0.0 0.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 0 0.0 0.0 35887_2019 35887 2019 4 3.3333333333333335 10.0 0.0 0.0 0 0.0 0.0 1 4.0 4.0 0.0 0.0 0 0.0 0.0 839649_2021 839649 2021 1 0.0 0.0 0.0 0.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 0 0.0 0.0 69834_2021 69834 2021 6 3.3333333333333335 24.0 2.6666666666666665 18.0 1 3.0 3.0 1 2.0 2.0 3.0 3.0 1 4.0 4.0 55379_2019 55379 2019 19 0.7631578947368421 29.0 0.0 0.0 5 1.4 7.0 3 0.0 0.0 0.0 0.0 1 3.0 3.0 54478_2020 54478 2020 5 2.4 12.0 3.0 12.0 1 3.0 3.0 1 2.0 2.0 4.0 4.0 1 3.0 3.0 863412_2023 863412 2023 2 3.5 7.0 3.0 6.0 1 3.0 3.0 1 4.0 4.0 3.0 3.0 0 0.0 0.0 60218_2019 60218 2019 4 2.5 10.0 1.25 5.0 1 2.0 2.0 1 2.0 2.0 2.0 2.0 1 4.0 4.0 44210_2021 44210 2021 6 2.6666666666666665 16.0 2.6666666666666665 16.0 0 0.0 0.0 1 4.0 4.0 4.0 4.0 1 2.0 2.0 58569_2020 58569 2020 5 2.4 16.0 3.4 21.0 1 2.0 2.0 2 4.0 8.0 4.0 8.0 1 2.0 2.0 840938_2019 840938 2019 1 0.0 0.0 3.0 3.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 0 0.0 0.0 847246_2020 847246 2020 2 2.0 4.0 3.0 6.0 0 0.0 0.0 1 2.0 2.0 3.0 3.0 0 0.0 0.0 50680_2017 50680 2017 5 3.0 15.0 0.0 0.0 0 0.0 0.0 1 3.0 3.0 0.0 0.0 1 3.0 3.0 3422_2013 3422 2013 3 2.1666666666666665 17.0 1.5833333333333333 12.0 2 3.0 6.0 4 2.5 10.0 1.75 7.0 1 1.0 1.0 36469_2018 36469 2018 4 2.0 8.0 2.5 10.0 1 1.0 1.0 0 0.0 0.0 0.0 0.0 1 3.0 3.0 62171_2021 62171 2021 2 2.5 5.0 2.0 4.0 0 0.0 0.0 1 3.0 3.0 2.0 2.0 1 2.0 2.0 1184_2023 1184 2023 5 2.8 14.0 2.2 11.0 0 0.0 0.0 1 4.0 4.0 2.0 2.0 1 0.0 0.0 54110_2017 54110 2017 5 1.8 11.0 0.0 0.0 1 1.0 1.0 2 2.0 4.0 0.0 0.0 1 1.0 1.0 54461_2017 54461 2017 2 2.0 4.0 0.0 0.0 0 0.0 0.0 1 1.0 1.0 0.0 0.0 1 3.0 3.0 54388_2022 54388 2022 3 2.6666666666666665 8.0 2.0 6.0 0 0.0 0.0 1 3.0 3.0 2.0 2.0 1 3.0 3.0 54637_2020 54637 2020 3 3.0 9.0 3.3333333333333335 10.0 0 0.0 0.0 1 2.0 2.0 3.0 3.0 1 3.0 3.0 44299_2021 44299 2021 3 2.6666666666666665 9.0 3.3333333333333335 12.0 0 0.0 0.0 1 4.0 4.0 4.0 4.0 0 0.0 0.0 54605_2022 54605 2022 2 2.5 8.0 2.0 6.0 0 0.0 0.0 1 2.0 2.0 2.0 2.0 0 0.0 0.0 35898_2023 35898 2023 4 2.5 10.0 2.0 8.0 1 2.0 2.0 1 2.0 2.0 2.0 2.0 1 3.0 3.0 834120_2022 834120 2022 1 1.0 1.0 0.0 0.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 1 1.0 1.0 31051_2020 31051 2020 5 2.8 14.0 2.6 13.0 0 0.0 0.0 1 3.0 3.0 2.0 2.0 1 2.0 2.0 859164_2021 859164 2021 1 0.0 0.0 0.0 0.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 0 0.0 0.0 60546_2017 60546 2017 1 0.0 0.0 0.0 0.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 0 0.0 0.0 859058_2021 859058 2021 1 0.0 0.0 0.0 0.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 0 0.0 0.0 49367_2021 49367 2021 4 3.0 12.0 3.5 14.0 1 4.0 4.0 0 0.0 0.0 0.0 0.0 1 2.0 2.0 43935_2023 43935 2023 4 2.5 10.0 2.0 8.0 1 2.0 2.0 1 3.0 3.0 2.0 2.0 1 2.0 2.0 55616_2018 55616 2018 3 2.3333333333333335 7.0 2.0 6.0 0 0.0 0.0 0 0.0 0.0 0.0 0.0 1 1.0 1.0 849052_2023 849052 2023 6 2.3000000000000003 33.0 2.0 26.0 0 0.0 0.0 2 3.0 6.0 2.0 4.0 0 0.0 0.0 31184_2015 31184 2015 2 3.5 7.0 4.0 8.0 1 4.0 4.0 1 3.0 3.0 4.0 4.0 0 0.0 0.0 31181_2014 31181 2014 7 2.2857142857142856 41.0 2.7142857142857144 49.0 1 1.0 1.0 6 3.0 18.0 3.3333333333333335 20.0 1 3.0 3.0 55800_2023 55800 2023 4 1.0 4.0 1.25 5.0 1 2.0 2.0 1 0.0 0.0 2.0 2.0 1 0.0 0.0 35274_2021 35274 2021 8 3.125 25.0 3.875 31.0 0 0.0 0.0 1 2.0 2.0 4.0 4.0 1 2.0 2.0 54632_2021 54632 2021 1 3.0 3.0 4.0 4.0 0 0.0 0.0 0 

Databricks visualization. Run in Databricks to view.

In [0]:
# Save dataframe as table in catalog default
df_climate_hazards.write.mode("overwrite").saveAsTable("default.df_climate_hazards")

# Save as CSV file in blob container
#storage_account_name = 'stgaclnrmlab'
#storage_account_access_key = 'rf/4ogYc/eG+oqVD8K9xjsVamosf1qO1s0Kab+ujHsTt0GjaGY2XHfXFNVdti4iaUndCJjNSqizi+ASt8IWqHw=='
#spark.conf.set('fs.azure.account.key.' + storage_account_name + '.blob.core.windows.net', storage_account_access_key)
#
#blob_container = 'citiesrespones'
#file_path = "wasbs://" + blob_container + "@" + storage_account_name + ".blob.core.windows.net/df_climate_hazards.csv.gz"
#
## Escribir el DataFrame en un archivo CSV comprimido en Azure Blob Storage
#df_climate_hazards.write.csv(file_path, compression='gzip', header=True)

In [0]:
df_climate_hazards_c = df_climate_hazards.groupBy('account') \
    .agg(
    count('*').alias('count'))

df_climate_hazards_c.count()